In [1]:
# takes 2h for 1,300,000 hand records
# perform experiments on standardized hand records.

# next steps:
# acbl-hand-records-chart-experiments.ipynb experiments with the trained data

# previous steps:
# acbl-hand-records.ipynb created acbl-hand-records.pkl

# todo:
# save model predictions
# let model know North hands. how? in terms of one hot 52 cards or 13/suit? QT? 
# plot accuracy of model
# remove all metrics except m.score?
# remove obsolete validation_df from model
# try feature scaling to improve accuracy?
# try changing activation function to sigmod/tanh/relu
# try using scikit's optimizer to try out various models.

# models:
# how often can expert bridge players predict dd? how can this be determined?
# create model to predict par score. different than dd?
# vary dd, hcp, sl to see how it effects predictions.
# chart of dd given sl and hcp is important. how does chart compare to predictions?
# show accuracy for each model

In [2]:
import pandas as pd
import pathlib
import pickle
import re
from collections import defaultdict
from IPython.display import display # needed to define display() method in vscode
import mlBridgeLib

In [3]:
# override pandas display options
mlBridgeLib.pd_options_display()

In [4]:
rootPath = pathlib.Path('e:/bridge/data')
acblPath = rootPath.joinpath('acbl')
savedModelsPath = acblPath.joinpath('SavedModels')
# create parent directories in case they don't already exist.
savedModelsPath.mkdir(parents=True, exist_ok=True)

In [5]:
# takes 15s (varies greatly) for 2,700,000 rows.
# read file containing boards which were reported by both acbl and tcg.
standardized_hand_records = acblPath.joinpath('acbl_hand_records.pkl')
df = pd.read_pickle(standardized_hand_records)
display(len(df),df.info(),df)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2761991 entries, 0 to 2767726
Data columns (total 11 columns):
 #   Column               Dtype 
---  ------               ----- 
 0   ref                  object
 1   hand_record_id       object
 2   event_id             int64 
 3   Board                string
 4   EventBoard           string
 5   Dealer               object
 6   Vul                  object
 7   board_record_string  object
 8   Hands                object
 9   Par                  object
 10  DDmakes              object
dtypes: int64(1), object(8), string(2)
memory usage: 252.9+ MB


2761991

None

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                                Par                                                                         DDmakes
0        (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                         (100, [(4, S, *, EW, -1)])        ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))
1        (acbl, 2620412)          77908    100961    20  200217A_20      W  Both  ST85HKJDJ43CKJ873SQ32HA643DK96CT94SAJ64HT98DT75CA52SK97HQ752DAQ82CQ6  ((T85, KJ, J43, KJ873), (AJ64, T98, T75, A52), (K97, Q752, AQ82, Q6), (Q32, A643, K96, T94))          (90, [(1, D, , NS, 1), (1, C, , NS, 1), (1, N, , NS, 0)])            ((8, 8, 7, 7, 7), (4, 5, 6, 6, 6), (8, 8, 7, 7, 7), (4, 5, 6, 6, 6))
2        (acbl, 2620411)          77908    100961    19  200217A_19      S   E_W  STH764DAQ92CQJ653SQJ763HKJTD65CAKTSK984H5DT8743C987SA52HAQ9832DKJC42  ((T, 764, AQ92, QJ653), (K984, 5, T8743, 987), (A52, AQ9832, KJ, 42), (QJ763, KJT, 65, AKT))                                         (100, [(3, S, *, EW, -1)])            ((9, 7, 9, 4, 6), (4, 6, 3, 8, 6), (9, 7, 9, 5, 6), (4, 6, 3, 8, 6))
3        (acbl, 2620420)          77908    100961    28  200217A_28      W   N_S  STHQJ9632DJ9CJ932SKQH8DQT86542CT76SJ76HATDAK3CAKQ84SA985432HK754D7C5  ((T, QJ9632, J9, J932), (J76, AT, AK3, AKQ84), (A985432, K754, 7, 5), (KQ, 8, QT86542, T76))                                        (-300, [(6, H, *, NS, -2)])    ((1, 0, 10, 8, 1), (11, 11, 3, 5, 11), (0, 0, 10, 8, 0), (11, 11, 3, 5, 11))
4        (acbl, 2620399)          77908    100961    07  200217A_07      S  Both  S2HQT762D92CAKT92SAKJ7HA8DKJ4C8643SQT854HK43DA765CQS963HJ95DQT83CJ75  ((2, QT762, 92, AKT92), (QT854, K43, A765, Q), (963, J95, QT83, J75), (AKJ7, A8, KJ4, 8643))                                         (-1430, [(6, S, , EW, 0)])        ((6, 2, 6, 1, 3), (7, 11, 6, 12, 8), (6, 2, 6, 1, 3), (7, 11, 6, 12, 8))
5        (acbl, 2620396)          77908    100961    04  200217A_04      W  Both  S84HAKJ83D4CQT743SA65HQ62DQ8732CK8SJ972HT5DAKJ96C95SKQT3H974DT5CAJ62  ((84, AKJ83, 4, QT743), (J972, T5, AKJ96, 95), (KQT3, 974, T5, AJ62), (A65, Q62, Q8732, K8))                                           (620, [(4, H, , NS, 0)])        ((10, 5, 10, 6, 6), (3, 8, 3, 6, 6), (10, 5, 10, 6, 6), (3, 8, 3, 6, 6))
6        (acbl, 2620410)          77908    100961    18  200217A_18      E   N_S  S872HJ8753DQ873CASAJ65HQ4DAKJ4C874S93HAK6D962CQT963SKQT4HT92DT5CKJ52  ((872, J8753, Q873, A), (93, AK6, 962, QT963), (KQT4, T92, T5, KJ52), (AJ65, Q4, AKJ4, 874))                                          (-120, [(1, N, , EW, 1)])            ((4, 4, 5, 5, 5), (9, 8, 7, 7, 8), (4, 5, 5, 5, 5), (9, 8, 7, 7, 8))
7        (acbl, 2620400)          77908    100961    08  200217A_08      W  None  S953H98642DJ9CKJ5SAJT6HAJ3DT2CAT96S742HKQ7DK764CQ43SKQ8HT5DAQ853C872  ((953, 98642, J9, KJ5), (742, KQ7, K764, Q43), (KQ8, T5, AQ853, 872), (AJT6, AJ3, T2, AT96))                                           (-140, [(1, S, , E, 2)])            ((4, 6, 6, 4, 5), (8, 7, 7, 9, 8), (4, 6, 6, 4, 5), (8, 7, 7, 8, 8))
8        (acbl, 2620397)          77908    100961    05  200217A_05      N   N_S  S98HAKT83D84CAQ82SQJHQJ65DT2CJ7653SAK752H72DAK96CKTST643H94DQJ753C94  ((98, AKT83, 84, AQ82), (AK752, 72, AK96, KT), (T643, 94, QJ753, 94), (QJ, QJ65, T2, J7653))                                          (-120, [(2, N, , EW, 0)])            ((5, 6, 7, 4, 5), (7, 7, 6, 8, 8), (5, 6, 7, 4, 5), (7, 7, 6, 8, 8))
9        (acbl, 2620398)          77908    100961    06  200217A_06      E   E_W  SA53HJT8DQ8743CQ9SK

In [6]:
augmented_df = df.copy().reset_index(drop=True) # must reset index so list appends sync properly
del df

In [7]:
# takes 30s
# Create columns of double dummy by direction by suit. e.g. DD_N_C.
def Augment_DDmakes(ddmakes):
    ddmakesd = defaultdict(list)
    for dd in ddmakes:
        for direction,nesw in zip(mlBridgeLib.NESW,dd):
            for suit,cdhsn in zip(mlBridgeLib.CDHSN,nesw):
                assert cdhsn is not None
                ddmakesd['_'.join(['DD',direction,suit])].append(cdhsn)
    return ddmakesd

ddmakesd = Augment_DDmakes(augmented_df['DDmakes'])
ddmakesdf = pd.DataFrame(ddmakesd,dtype='int8')
display(ddmakesdf.dtypes,ddmakesdf.head())
assert len(augmented_df) == len(ddmakesdf)
augmented_df = pd.concat([augmented_df,ddmakesdf],axis='columns',join='inner')
del ddmakesdf,ddmakesd
display(augmented_df.dtypes,augmented_df)

DD_N_C    int8
DD_N_D    int8
DD_N_H    int8
DD_N_S    int8
DD_N_N    int8
DD_E_C    int8
DD_E_D    int8
DD_E_H    int8
DD_E_S    int8
DD_E_N    int8
DD_S_C    int8
DD_S_D    int8
DD_S_H    int8
DD_S_S    int8
DD_S_N    int8
DD_W_C    int8
DD_W_D    int8
DD_W_H    int8
DD_W_S    int8
DD_W_N    int8
dtype: object

DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N
0      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2
1       8       8       7       7       7       4       5       6       6       6       8       8       7       7       7       4       5       6       6       6
2       9       7       9       4       6       4       6       3       8       6       9       7       9       5       6       4       6       3       8       6
3       1       0      10       8       1      11      11       3       5      11       0       0      10       8       0      11      11       3       5      11
4       6       2       6       1       3       7      11       6      12       8       6       2       6       1       3       7      11       6      12       8

ref                    object
hand_record_id         object
event_id                int64
Board                  string
EventBoard             string
Dealer                 object
Vul                    object
board_record_string    object
Hands                  object
Par                    object
DDmakes                object
DD_N_C                   int8
DD_N_D                   int8
DD_N_H                   int8
DD_N_S                   int8
DD_N_N                   int8
DD_E_C                   int8
DD_E_D                   int8
DD_E_H                   int8
DD_E_S                   int8
DD_E_N                   int8
DD_S_C                   int8
DD_S_D                   int8
DD_S_H                   int8
DD_S_S                   int8
DD_S_N                   int8
DD_W_C                   int8
DD_W_D                   int8
DD_W_H                   int8
DD_W_S                   int8
DD_W_N                   int8
dtype: object

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                                Par                                                                         DDmakes  DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N
0        (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                         (100, [(4, S, *, EW, -1)])        ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2
1        (acbl, 2620412)          77908    100961    20  200217A_20      W  Both  ST85HKJDJ43CKJ873SQ32HA643DK96CT94SAJ64HT98DT75CA52SK97HQ752DAQ82CQ6  ((T85, KJ, J43, KJ873), (AJ64, T98, T75, A52), (K97, Q752, AQ82, Q6), (Q32, A643, K96, T94))          (90, [(1, D, , NS, 1), (1, C, , NS, 1), (1, N, , NS, 0)])            ((8, 8, 7, 7, 7), (4, 5, 6, 6, 6), (8, 8, 7, 7, 7), (4, 5, 6, 6, 6))       8       8       7       7       7       4       5       6       6       6       8       8       7       7       7       4       5       6       6       6
2        (acbl, 2620411)          77908    100961    19  200217A_19      S   E_W  STH764DAQ92CQJ653SQJ763HKJTD65CAKTSK984H5DT8743C987SA52HAQ9832DKJC42  ((T, 764, AQ92, QJ653), (K984, 5, T8743, 987), (A52, AQ9832, KJ, 42), (QJ763, KJT, 65, AKT))                                         (100, [(3, S, *, EW, -1)])            ((9, 7, 9, 4, 6), (4, 6, 3, 8, 6), (9, 7, 9, 5, 6), (4, 6, 3, 8, 6))       9       7       9       4       6       4       6       3       8       6       9       7       9       5       6       4       6       3       8       6
3        (acbl, 2620420)          77908    100961    28  200217A_28      W   N_S  STHQJ9632DJ9CJ932SKQH8DQT86542CT76SJ76HATDAK3CAKQ84SA985432HK754D7C5  ((T, QJ9632, J9, J932), (J76, AT, AK3, AKQ84), (A985432, K754, 7, 5), (KQ, 8, QT86542, T76))                                        (-300, [(6, H, *, NS, -2)])    ((1, 0, 10, 8, 1), (11, 11, 3, 5, 11), (0, 0, 10, 8, 0), (11, 11, 3, 5, 11))       1       0      10       8       1      11      11       3       5      11       0       0      10       8       0      11      11       3       5      11
4        (acbl, 2620399)          77908    100961    07  200217A_07      S  Both  S2HQT762D92CAKT92SAKJ7HA8DKJ4C8643SQT854HK43DA765CQS963HJ95DQT83CJ75  ((2, QT762, 92, AKT92), (QT854, K43, A765, Q), (963, J95, QT83, J75), (AKJ7, A8, KJ4, 8643))                                         (-1430, [(6, S, , EW, 0)])        ((6, 2, 6, 1, 3), (7, 11, 6, 12, 8), (6, 2, 6, 1, 3), (7, 11, 6, 12, 8))       6       2       6       1       3       7      11       6      12       8       6       2       6       1       3       7      11       6      12       8
5        (acbl, 2620396)          77908    100961    04  200217A_04      W  Both  S84HAKJ83D4CQT743SA65HQ62DQ8732CK8SJ972HT5DAKJ96C95SKQT3H974DT5CAJ62  ((84, AKJ83, 4, QT743), (J972, T5, AKJ96, 95), (KQT3, 974, T5, AJ62), (A65, Q62, Q8732, K8))                                           (620, [(4, H, , NS, 0)])        ((10, 5, 10, 6, 6), (3, 8, 3, 6, 6), (10, 5, 10, 6, 6), (3, 8, 3, 6, 6))      10       5      10       6       6       3       8       3       6       6      10       5      10       6       6       3       8       3       6       6
6        (acbl, 2620410)          77908    100961    18  200217A_18      E   N_S  S872HJ8753DQ873CASAJ65HQ4DAKJ4C874S93HAK6D962CQT963SKQT4HT92DT5CKJ52  ((872

In [8]:
# takes 1m15s
# create column of Hands expressed in binary.
assert 'Hands_Bin' not in augmented_df.columns
augmented_df['Hands_Bin'] = augmented_df['Hands'].map(mlBridgeLib.HandsToBin)
augmented_df.head()

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                        Par                                                                       DDmakes  DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N                                                                                            Hands_Bin
0  (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                 (100, [(4, S, *, EW, -1)])      ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2  ((0b100010000010000000001100010000000011001011100100, (0b100010000, 0b100000000011, 0b1000000001...
1  (acbl, 2620412)          77908    100961    20  200217A_20      W  Both  ST85HKJDJ43CKJ873SQ32HA643DK96CT94SAJ64HT98DT75CA52SK97HQ752DAQ82CQ6  ((T85, KJ, J43, KJ873), (AJ64, T98, T75, A52), (K97, Q752, AQ82, Q6), (Q32, A643, K96, T94))  (90, [(1, D, , NS, 1), (1, C, , NS, 1), (1, N, , NS, 0)])          ((8, 8, 7, 7, 7), (4, 5, 6, 6, 6), (8, 8, 7, 7, 7), (4, 5, 6, 6, 6))       8       8       7       7       7       4       5       6       6       6       8       8       7       7       7       4       5       6       6       6  ((0b101001000010100000000000010000001100101001100010, (0b101001000, 0b101000000000, 0b1000000110...
2  (acbl, 2620411)          77908    100961    19  200217A_19      S   E_W  STH764DAQ92CQJ653SQJ763HKJTD65CAKTSK984H5DT8743C987SA52HAQ9832DKJC42  ((T, 764, AQ92, QJ653), (K984, 5, T8743, 987), (A52, AQ9832, KJ, 42), (QJ763, KJT, 65, AKT))                                 (100, [(3, S, *, EW, -1)])          ((9, 7, 9, 4, 6), (4, 6, 3, 8, 6), (9, 7, 9, 5, 6), (4, 6, 3, 8, 6))       9       7       9       4       6       4       6       3       8       6       9       7       9       5       6       4       6       3       8       6  ((0b100000000000000011010010100100000010011000011010, (0b100000000, 0b110100, 0b1010010000001, 0...
3  (acbl, 2620420)          77908    100961    28  200217A_28      W   N_S  STHQJ9632DJ9CJ932SKQH8DQT86542CT76SJ76HATDAK3CAKQ84SA985432HK754D7C5  ((T, QJ9632, J9, J932), (J76, AT, AK3, AKQ84), (A985432, K754, 7, 5), (KQ, 8, QT86542, T76))                                (-300, [(6, H, *, NS, -2)])  ((1, 0, 10, 8, 1), (11, 11, 3, 5, 11), (0, 0, 10, 8, 0), (11, 11, 3, 5, 11))       1       0      10       8       1      11      11       3       5      11       0       0      10       8       0      11      11       3       5      11  ((0b100000000001101001001100010100000000001010000011, (0b100000000, 0b11010010011, 0b1010000000,...
4  (acbl, 2620399)          77908    100961    07  200217A_07      S  Both  S2HQT762D92CAKT92SAKJ7HA8DKJ4C8643SQT854HK43DA765CQS963HJ95DQT83CJ75  ((2, QT762, 92, AKT92), (QT854, K43, A765, Q), (963, J95, QT83, J75), (AKJ7, A8, KJ4, 8643))                                 (-1430, [(6, S, , EW, 0)])      ((6, 2, 6, 1, 3), (7, 11, 6, 12, 8), (6, 2, 6, 1, 3), (7, 11, 6, 12, 8))       6       2       6       1       3       7      11       6      12       8       6       2       6       1       3       7      11       6      12       8  ((0b1001010011000100000100000011100110000001, (0b1, 0b10100110001, 0b10000001, 0b1100110000001))...

In [9]:
# takes 8s
# Create one hot encoding, length 52, for each direction's hand.
# todo: one hot encode each direction's hand? Leaving as binary string for now.
def OHE_Hands(hands_bin):
    handsbind = defaultdict(list)
    for h in hands_bin:
        for direction,nesw in zip(mlBridgeLib.NESW,h):
            assert nesw[0] is not None and nesw[1] is not None
            handsbind['_'.join(['HB',direction])].append(nesw[0]) # todo: int(nesw[0],2)) # convert binary string to base 2 int
            #for suit,shdc in zip(mlBridgeLib.SHDC,nesw[1]):
            #    assert shdc is not None
            #    handsbind['_'.join(['HCP',direction,suit])].append(shdc)
    return handsbind

handsbind = OHE_Hands(augmented_df['Hands_Bin'])
handsbindf = pd.DataFrame(handsbind,dtype='string') # need 52 bits
display(handsbindf.dtypes,len(handsbindf),len(augmented_df),handsbindf.head())
assert len(augmented_df) == len(handsbindf)
augmented_df = pd.concat([augmented_df,handsbindf],axis='columns',join='inner')
del handsbindf,handsbind
display(augmented_df.dtypes,augmented_df)

HB_N    string
HB_E    string
HB_S    string
HB_W    string
dtype: object

2761991

2761991

HB_N                                                    HB_E                                                    HB_S                                                    HB_W
0  0b100010000010000000001100010000000011001011100100  0b1000001001010001000000000001100100100100100000001001   0b100000100000100111100010010000000010000000100010010    0b11010000101000000011100000001011001000010000000000
1  0b101001000010100000000000010000001100101001100010  0b1001000010100000011100000000001001010001000000001001   0b100010100000001000010100110100010000010010000010000    0b10000000011100000001011001000100100000000110000100
2  0b100000000000000011010010100100000010011000011010   0b100011000100000000000100000001011001100000011100000  0b1000000001001101001100001101010000000000000000000101    0b11000110010010110000000000000000110001100100000000
3  0b100000000001101001001100010100000000001010000011     0b1000110000100010000000011000000000101110001000100  0b1000011001111010000010110000000001000000000000001000   0b110000000000000000100000000101010111010000100110000
4          0b1001010011000100000100000011100110000001    0b10101001100010000000011010000001110000010000000000       0b10010010000101000100000101010000100001000101000  0b1101000100000100000100000001010000001000000001010110

ref                    object
hand_record_id         object
event_id                int64
Board                  string
EventBoard             string
Dealer                 object
Vul                    object
board_record_string    object
Hands                  object
Par                    object
DDmakes                object
DD_N_C                   int8
DD_N_D                   int8
DD_N_H                   int8
DD_N_S                   int8
DD_N_N                   int8
DD_E_C                   int8
DD_E_D                   int8
DD_E_H                   int8
DD_E_S                   int8
DD_E_N                   int8
DD_S_C                   int8
DD_S_D                   int8
DD_S_H                   int8
DD_S_S                   int8
DD_S_N                   int8
DD_W_C                   int8
DD_W_D                   int8
DD_W_H                   int8
DD_W_S                   int8
DD_W_N                   int8
Hands_Bin              object
HB_N                   string
HB_E      

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                                Par                                                                         DDmakes  DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N                                                                                            Hands_Bin                                                    HB_N                                                    HB_E                                                    HB_S                                                    HB_W
0        (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                         (100, [(4, S, *, EW, -1)])        ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2  ((0b100010000010000000001100010000000011001011100100, (0b100010000, 0b100000000011, 0b1000000001...      0b100010000010000000001100010000000011001011100100  0b1000001001010001000000000001100100100100100000001001   0b100000100000100111100010010000000010000000100010010    0b11010000101000000011100000001011001000010000000000
1        (acbl, 2620412)          77908    100961    20  200217A_20      W  Both  ST85HKJDJ43CKJ873SQ32HA643DK96CT94SAJ64HT98DT75CA52SK97HQ752DAQ82CQ6  ((T85, KJ, J43, KJ873), (AJ64, T98, T75, A52), (K97, Q752, AQ82, Q6), (Q32, A643, K96, T94))          (90, [(1, D, , NS, 1), (1, C, , NS, 1), (1, N, , NS, 0)])            ((8, 8, 7, 7, 7), (4, 5, 6, 6, 6), (8, 8, 7, 7, 7), (4, 5, 6, 6, 6))       8       8       7       7       7       4       5       6       6       6       8       8       7       7       7       4       5       6       6       6  ((0b101001000010100000000000010000001100101001100010, (0b101001000, 0b101000000000, 0b1000000110...      0b101001000010100000000000010000001100101001100010  0b1001000010100000011100000000001001010001000000001001   0b100010100000001000010100110100010000010010000010000    0b10000000011100000001011001000100100000000110000100
2        (acbl, 2620411)          77908    100961    19  200217A_19      S   E_W  STH764DAQ92CQJ653SQJ763HKJTD65CAKTSK984H5DT8743C987SA52HAQ9832DKJC42  ((T, 764, AQ92, QJ653), (K984, 5, T8743, 987), (A52, AQ9832, KJ, 42), (QJ763, KJT, 65, AKT))                                         (100, [(3, S, *, EW, -1)])            ((9, 7, 9, 4, 6), (4, 6, 3, 8, 6), (9, 7, 9, 5, 6), (4, 6, 3, 8, 6))       9       7       9       4       6       4       6       3       8       6       9       7       9       5       6       4       6       3       8       6  ((0b100000000000000011010010100100000010011000011010, (0b100000000, 0b110100, 0b1010010000001, 0...      0b100000000000000011010010100100000010011000011010   0b100011000100000000000100000001011001100000011100000  0b1000000001001101001100001101010000000000000000000101    0b11000110010010110000000000000000110001100100000000
3        (acbl, 2620420)          77908    100961    28  200217A_28      W   N_S  STHQJ9632DJ9CJ932SKQH8DQT86542CT76SJ76HATDAK3CAKQ84SA985432HK754D7C5  ((T, QJ9632, J9, J932), (J76, AT, AK3, AKQ84), (A985432, K754, 7, 5), (KQ, 8, QT86542, T76))                                        (-300, [(6, H, *, NS, -2)])    ((1, 0, 10, 8, 1), (11, 11, 3, 5, 11), (0, 0, 10, 8, 0), (11, 11, 3, 5, 11))       1       0      10       8       1      11      11       3       5      11       0       0      10       8       0  

In [10]:
# takes 45s
# Compute HCPs from board numbers. Validate against any existing HCP column.
assert 'HCP' not in augmented_df.columns
augmented_df['HCP'] = augmented_df['Hands'].map(mlBridgeLib.HandsToHCP)

In [11]:
# takes 35s
# Compute HCP per direction, per suit.
def Augment_HCP(hcps):
    hcpsd = defaultdict(list)
    for h in hcps:
        for direction,nesw in zip(mlBridgeLib.NESW,h):
            assert nesw[0] is not None and nesw[1] is not None
            hcpsd['_'.join(['HCP',direction])].append(nesw[0])
            for suit,shdc in zip(mlBridgeLib.SHDC,nesw[1]):
                assert shdc is not None
                hcpsd['_'.join(['HCP',direction,suit])].append(shdc)
    return hcpsd

hcpsd = Augment_HCP(augmented_df['HCP'])
hcpsdf = pd.DataFrame(hcpsd,dtype='int8')
display(hcpsdf.dtypes,hcpsdf.head())
assert len(augmented_df) == len(hcpsdf)
augmented_df = pd.concat([augmented_df,hcpsdf],axis='columns',join='inner')
del hcpsdf,hcpsd
display(augmented_df.dtypes,augmented_df)

HCP_N      int8
HCP_N_S    int8
HCP_N_H    int8
HCP_N_D    int8
HCP_N_C    int8
HCP_E      int8
HCP_E_S    int8
HCP_E_H    int8
HCP_E_D    int8
HCP_E_C    int8
HCP_S      int8
HCP_S_S    int8
HCP_S_H    int8
HCP_S_D    int8
HCP_S_C    int8
HCP_W      int8
HCP_W_S    int8
HCP_W_H    int8
HCP_W_D    int8
HCP_W_C    int8
dtype: object

HCP_N  HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  HCP_E  HCP_E_S  HCP_E_H  HCP_E_D  HCP_E_C  HCP_S  HCP_S_S  HCP_S_H  HCP_S_D  HCP_S_C  HCP_W  HCP_W_S  HCP_W_H  HCP_W_D  HCP_W_C
0      9        0        3        1        5     14        4        2        5        3     12        3        5        4        0      5        3        0        0        2
1      9        0        4        1        4      9        5        0        0        4     13        3        2        6        2      9        2        4        3        0
2      9        0        0        6        3      3        3        0        0        0     14        4        6        4        0     14        3        4        0        7
3      5        0        3        1        1     21        1        4        7        9      7        4        3        0        0      7        5        0        2        0
4      9        0        2        0        7     11        2        3        4        2      4        0        1        2        1     16        8        4        4        0

ref                    object
hand_record_id         object
event_id                int64
Board                  string
EventBoard             string
Dealer                 object
Vul                    object
board_record_string    object
Hands                  object
Par                    object
DDmakes                object
DD_N_C                   int8
DD_N_D                   int8
DD_N_H                   int8
DD_N_S                   int8
DD_N_N                   int8
DD_E_C                   int8
DD_E_D                   int8
DD_E_H                   int8
DD_E_S                   int8
DD_E_N                   int8
DD_S_C                   int8
DD_S_D                   int8
DD_S_H                   int8
DD_S_S                   int8
                        ...  
HB_N                   string
HB_E                   string
HB_S                   string
HB_W                   string
HCP                    object
HCP_N                    int8
HCP_N_S                  int8
HCP_N_H   

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                                Par                                                                         DDmakes  DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N                                                                                            Hands_Bin                                                    HB_N                                                    HB_E                                                    HB_S                                                    HB_W                                                                              HCP  HCP_N  HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  HCP_E  HCP_E_S  HCP_E_H  HCP_E_D  HCP_E_C  HCP_S  HCP_S_S  HCP_S_H  HCP_S_D  HCP_S_C  HCP_W  HCP_W_S  HCP_W_H  HCP_W_D  HCP_W_C
0        (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                         (100, [(4, S, *, EW, -1)])        ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2  ((0b100010000010000000001100010000000011001011100100, (0b100010000, 0b100000000011, 0b1000000001...      0b100010000010000000001100010000000011001011100100  0b1000001001010001000000000001100100100100100000001001   0b100000100000100111100010010000000010000000100010010    0b11010000101000000011100000001011001000010000000000   ((9, (0, 3, 1, 5)), (14, (4, 2, 5, 3)), (12, (3, 5, 4, 0)), (5, (3, 0, 0, 2)))      9        0        3        1        5     14        4        2        5        3     12        3        5        4        0      5        3        0        0        2
1        (acbl, 2620412)          77908    100961    20  200217A_20      W  Both  ST85HKJDJ43CKJ873SQ32HA643DK96CT94SAJ64HT98DT75CA52SK97HQ752DAQ82CQ6  ((T85, KJ, J43, KJ873), (AJ64, T98, T75, A52), (K97, Q752, AQ82, Q6), (Q32, A643, K96, T94))          (90, [(1, D, , NS, 1), (1, C, , NS, 1), (1, N, , NS, 0)])            ((8, 8, 7, 7, 7), (4, 5, 6, 6, 6), (8, 8, 7, 7, 7), (4, 5, 6, 6, 6))       8       8       7       7       7       4       5       6       6       6       8       8       7       7       7       4       5       6       6       6  ((0b101001000010100000000000010000001100101001100010, (0b101001000, 0b101000000000, 0b1000000110...      0b101001000010100000000000010000001100101001100010  0b1001000010100000011100000000001001010001000000001001   0b100010100000001000010100110100010000010010000010000    0b10000000011100000001011001000100100000000110000100    ((9, (0, 4, 1, 4)), (9, (5, 0, 0, 4)), (13, (3, 2, 6, 2)), (9, (2, 4, 3, 0)))      9        0        4        1        4      9        5        0        0        4     13        3        2        6        2      9        2        4        3        0
2        (acbl, 2620411)          77908    100961    19  200217A_19      S   E_W  STH764DAQ92CQJ653SQJ763HKJTD65CAKTSK984H5DT8743C987SA52HAQ9832DKJC42  ((T, 764, AQ92, QJ653), (K984, 5, T8743, 987), (A52, AQ9832, KJ, 42), (QJ763, KJT, 65, AKT))                                         (100, [(3, S, *, EW, -1)])            ((9, 7, 9, 4, 6), (4, 6, 3, 8, 6), (9, 7, 9, 5, 6), (4, 6, 3, 8, 6))       9       7       9       4       6       4       6       3       8       6       9       7       9       5       6       4       6       3       8       6  ((0b100000000000000011010010100100000010011000011010, (0b100000000, 0b110100, 

In [12]:
# takes 50s
# Compute QTs from Hands
assert 'QT' not in augmented_df.columns
augmented_df['QT'] = augmented_df['Hands'].map(mlBridgeLib.HandsToQT)

In [13]:
# takes 35s
# Compute quick tricks per direction, per suit.
def Augment_QT(qts):
    qts_d = defaultdict(list)
    for qt in qts:
        for direction,nesw in zip(mlBridgeLib.NESW,qt[1]):
            assert nesw[0] is not None and nesw[1] is not None
            qts_d['_'.join(['QT',direction])].append(nesw[0]) # qt total per direction
            for suit,shdc in zip(mlBridgeLib.SHDC,nesw[1]):
                assert shdc is not None
                qts_d['_'.join(['QT',direction,suit])].append(shdc) # qt per direction per suit
    return qts_d

qts_d = Augment_QT(augmented_df['QT'])
qts_df = pd.DataFrame(qts_d,dtype='float32')
display(qts_df.dtypes,qts_df.head())
assert len(augmented_df) == len(qts_df)
augmented_df = pd.concat([augmented_df,qts_df],axis='columns',join='inner')
del qts_df,qts_d
display(augmented_df.dtypes,augmented_df)

QT_N      float32
QT_N_S    float32
QT_N_H    float32
QT_N_D    float32
QT_N_C    float32
QT_E      float32
QT_E_S    float32
QT_E_H    float32
QT_E_D    float32
QT_E_C    float32
QT_S      float32
QT_S_S    float32
QT_S_H    float32
QT_S_D    float32
QT_S_C    float32
QT_W      float32
QT_W_S    float32
QT_W_H    float32
QT_W_D    float32
QT_W_C    float32
dtype: object

QT_N  QT_N_S  QT_N_H  QT_N_D  QT_N_C  QT_E  QT_E_S  QT_E_H  QT_E_D  QT_E_C  QT_S  QT_S_S  QT_S_H  QT_S_D  QT_S_C  QT_W  QT_W_S  QT_W_H  QT_W_D  QT_W_C
0  1.50    0.00    0.50    0.00    1.00  2.50    1.00    0.00    1.00    0.50  2.50    0.50    1.00    1.00    0.00  0.00    0.00    0.00    0.00    0.00
1  1.00    0.00    0.50    0.00    0.50  2.00    1.00    0.00    0.00    1.00  2.00    0.50    0.00    1.50    0.00  1.50    0.00    1.00    0.50    0.00
2  1.50    0.00    0.00    1.50    0.00  0.50    0.50    0.00    0.00    0.00  3.00    1.00    1.50    0.50    0.00  2.50    0.00    0.50    0.00    2.00
3  0.00    0.00    0.00    0.00    0.00  5.00    0.00    1.00    2.00    2.00  1.50    1.00    0.50    0.00    0.00  1.00    1.00    0.00    0.00    0.00
4  2.00    0.00    0.00    0.00    2.00  1.50    0.00    0.50    1.00    0.00  0.00    0.00    0.00    0.00    0.00  3.50    2.00    1.00    0.50    0.00

ref                     object
hand_record_id          object
event_id                 int64
Board                   string
EventBoard              string
Dealer                  object
Vul                     object
board_record_string     object
Hands                   object
Par                     object
DDmakes                 object
DD_N_C                    int8
DD_N_D                    int8
DD_N_H                    int8
DD_N_S                    int8
DD_N_N                    int8
DD_E_C                    int8
DD_E_D                    int8
DD_E_H                    int8
DD_E_S                    int8
DD_E_N                    int8
DD_S_C                    int8
DD_S_D                    int8
DD_S_H                    int8
DD_S_S                    int8
                        ...   
HCP_W_S                   int8
HCP_W_H                   int8
HCP_W_D                   int8
HCP_W_C                   int8
QT                      object
QT_N                   float32
QT_N_S  

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                                Par                                                                         DDmakes  DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N                                                                                            Hands_Bin                                                    HB_N                                                    HB_E                                                    HB_S                                                    HB_W                                                                              HCP  HCP_N  HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  HCP_E  HCP_E_S  HCP_E_H  HCP_E_D  HCP_E_C  HCP_S  HCP_S_S  HCP_S_H  HCP_S_D  HCP_S_C  HCP_W  HCP_W_S  HCP_W_H  HCP_W_D  HCP_W_C                                                                                                   QT  QT_N  QT_N_S  QT_N_H  QT_N_D  QT_N_C  QT_E  QT_E_S  QT_E_H  QT_E_D  QT_E_C  QT_S  QT_S_S  QT_S_H  QT_S_D  QT_S_C  QT_W  QT_W_S  QT_W_H  QT_W_D  QT_W_C
0        (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                         (100, [(4, S, *, EW, -1)])        ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2  ((0b100010000010000000001100010000000011001011100100, (0b100010000, 0b100000000011, 0b1000000001...      0b100010000010000000001100010000000011001011100100  0b1000001001010001000000000001100100100100100000001001   0b100000100000100111100010010000000010000000100010010    0b11010000101000000011100000001011001000010000000000   ((9, (0, 3, 1, 5)), (14, (4, 2, 5, 3)), (12, (3, 5, 4, 0)), (5, (3, 0, 0, 2)))      9        0        3        1        5     14        4        2        5        3     12        3        5        4        0      5        3        0        0        2      (6.5, ((1.5, (0, 0.5, 0, 1)), (2.5, (1, 0, 1, 0.5)), (2.5, (0.5, 1, 1, 0)), (0, (0, 0, 0, 0))))  1.50    0.00    0.50    0.00    1.00  2.50    1.00    0.00    1.00    0.50  2.50    0.50    1.00    1.00    0.00  0.00    0.00    0.00    0.00    0.00
1        (acbl, 2620412)          77908    100961    20  200217A_20      W  Both  ST85HKJDJ43CKJ873SQ32HA643DK96CT94SAJ64HT98DT75CA52SK97HQ752DAQ82CQ6  ((T85, KJ, J43, KJ873), (AJ64, T98, T75, A52), (K97, Q752, AQ82, Q6), (Q32, A643, K96, T94))          (90, [(1, D, , NS, 1), (1, C, , NS, 1), (1, N, , NS, 0)])            ((8, 8, 7, 7, 7), (4, 5, 6, 6, 6), (8, 8, 7, 7, 7), (4, 5, 6, 6, 6))       8       8       7       7       7       4       5       6       6       6       8       8       7       7       7       4       5       6       6       6  ((0b101001000010100000000000010000001100101001100010, (0b101001000, 0b101000000000, 0b1000000110...      0b101001000010100000000000010000001100101001100010  0b1001000010100000011100000000001001010001000000001001   0b100010100000001000010100110100010000010010000010000    0b10000000011100000001011001000100100000000110000100    ((9, (0, 4, 1, 4)), (9, (5, 0, 0, 4)), (13, (3, 2, 6, 2)), (9, (2, 4, 3, 0)))      9        0        4        1        4      9        5        0        0        4     13        3        2        6        2      9        2        4        3        0  (6.5, ((1.0, (0, 0.5, 0, 0.5)), (2, (1, 0, 0, 1)), (2.0, (0.5, 0, 1.5, 0)), (1.5, (0, 1, 0.5, 0))))  1.00    0.00    0.50   

In [14]:
# takes 10s
# Compute QTs from Hands
assert 'Suit_Lengths' not in augmented_df.columns
augmented_df['Suit_Lengths'] = augmented_df['Hands'].map(mlBridgeLib.SuitLengths)

In [15]:
# takes 30s
# Compute suit lengths per direction, per suit.
def Augment_SuitLengths(suitlengths):
    suitlengthsd = defaultdict(list)
    for sl in suitlengths:
        for direction,nesw in zip(mlBridgeLib.NESW,sl):
            for suit,shdc in zip(mlBridgeLib.SHDC,nesw):
                assert shdc is not None
                suitlengthsd['_'.join(['SL',direction,suit])].append(shdc)
    return suitlengthsd

suitlengthsd = Augment_SuitLengths(augmented_df['Suit_Lengths'])
suitlengthsdf = pd.DataFrame(suitlengthsd,dtype='int8')
display(suitlengthsdf.dtypes,suitlengthsdf.head())
assert len(augmented_df) == len(suitlengthsdf)
augmented_df = pd.concat([augmented_df,suitlengthsdf],axis='columns',join='inner')
del suitlengthsdf,suitlengthsd
display(augmented_df.dtypes,augmented_df)

SL_N_S    int8
SL_N_H    int8
SL_N_D    int8
SL_N_C    int8
SL_E_S    int8
SL_E_H    int8
SL_E_D    int8
SL_E_C    int8
SL_S_S    int8
SL_S_H    int8
SL_S_D    int8
SL_S_C    int8
SL_W_S    int8
SL_W_H    int8
SL_W_D    int8
SL_W_C    int8
dtype: object

SL_N_S  SL_N_H  SL_N_D  SL_N_C  SL_E_S  SL_E_H  SL_E_D  SL_E_C  SL_S_S  SL_S_H  SL_S_D  SL_S_C  SL_W_S  SL_W_H  SL_W_D  SL_W_C
0       2       3       2       6       4       1       5       3       2       6       2       3       5       3       4       1
1       3       2       3       5       4       3       3       3       3       4       4       2       3       4       3       3
2       1       3       4       5       4       1       5       3       3       6       2       2       5       3       2       3
3       1       6       2       4       3       2       3       5       7       4       1       1       2       1       7       3
4       1       5       2       5       5       3       4       1       3       3       4       3       4       2       3       4

ref                     object
hand_record_id          object
event_id                 int64
Board                   string
EventBoard              string
Dealer                  object
Vul                     object
board_record_string     object
Hands                   object
Par                     object
DDmakes                 object
DD_N_C                    int8
DD_N_D                    int8
DD_N_H                    int8
DD_N_S                    int8
DD_N_N                    int8
DD_E_C                    int8
DD_E_D                    int8
DD_E_H                    int8
DD_E_S                    int8
DD_E_N                    int8
DD_S_C                    int8
DD_S_D                    int8
DD_S_H                    int8
DD_S_S                    int8
                        ...   
QT_S_H                 float32
QT_S_D                 float32
QT_S_C                 float32
QT_W                   float32
QT_W_S                 float32
QT_W_H                 float32
QT_W_D  

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                                Par                                                                         DDmakes  DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N                                                                                            Hands_Bin                                                    HB_N                                                    HB_E                                                    HB_S                                                    HB_W                                                                              HCP  HCP_N  HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  HCP_E  HCP_E_S  HCP_E_H  HCP_E_D  HCP_E_C  HCP_S  HCP_S_S  HCP_S_H  HCP_S_D  HCP_S_C  HCP_W  HCP_W_S  HCP_W_H  HCP_W_D  HCP_W_C                                                                                                   QT  QT_N  QT_N_S  QT_N_H  QT_N_D  QT_N_C  QT_E  QT_E_S  QT_E_H  QT_E_D  QT_E_C  QT_S  QT_S_S  QT_S_H  QT_S_D  QT_S_C  QT_W  QT_W_S  QT_W_H  QT_W_D  QT_W_C                                              Suit_Lengths  SL_N_S  SL_N_H  SL_N_D  SL_N_C  SL_E_S  SL_E_H  SL_E_D  SL_E_C  SL_S_S  SL_S_H  SL_S_D  SL_S_C  SL_W_S  SL_W_H  SL_W_D  SL_W_C
0        (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                         (100, [(4, S, *, EW, -1)])        ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2  ((0b100010000010000000001100010000000011001011100100, (0b100010000, 0b100000000011, 0b1000000001...      0b100010000010000000001100010000000011001011100100  0b1000001001010001000000000001100100100100100000001001   0b100000100000100111100010010000000010000000100010010    0b11010000101000000011100000001011001000010000000000   ((9, (0, 3, 1, 5)), (14, (4, 2, 5, 3)), (12, (3, 5, 4, 0)), (5, (3, 0, 0, 2)))      9        0        3        1        5     14        4        2        5        3     12        3        5        4        0      5        3        0        0        2      (6.5, ((1.5, (0, 0.5, 0, 1)), (2.5, (1, 0, 1, 0.5)), (2.5, (0.5, 1, 1, 0)), (0, (0, 0, 0, 0))))  1.50    0.00    0.50    0.00    1.00  2.50    1.00    0.00    1.00    0.50  2.50    0.50    1.00    1.00    0.00  0.00    0.00    0.00    0.00    0.00  ((2, 3, 2, 6), (4, 1, 5, 3), (2, 6, 2, 3), (5, 3, 4, 1))       2       3       2       6       4       1       5       3       2       6       2       3       5       3       4       1
1        (acbl, 2620412)          77908    100961    20  200217A_20      W  Both  ST85HKJDJ43CKJ873SQ32HA643DK96CT94SAJ64HT98DT75CA52SK97HQ752DAQ82CQ6  ((T85, KJ, J43, KJ873), (AJ64, T98, T75, A52), (K97, Q752, AQ82, Q6), (Q32, A643, K96, T94))          (90, [(1, D, , NS, 1), (1, C, , NS, 1), (1, N, , NS, 0)])            ((8, 8, 7, 7, 7), (4, 5, 6, 6, 6), (8, 8, 7, 7, 7), (4, 5, 6, 6, 6))       8       8       7       7       7       4       5       6       6       6       8       8       7       7       7       4       5       6       6       6  ((0b101001000010100000000000010000001100101001100010, (0b101001000, 0b101000000000, 0b1000000110...      0b101001000010100000000000010000001100101001100010  0b1001000010100000011100000000001001010001000000001001   0b100010100000001000010100110100010000010010000010000    0b10000000011100000001011001000100100000000110000100    ((9

In [16]:
# takes 15s
# Create columns for partnership (NS,EW). e.g. HCP_NS, HCP_EW, HCP_EW_C, ...
sum_ns_ew = [('HCP','int8'), ('QT','float32'), ('SL','int8')]
for c,t in sum_ns_ew:
    for d in mlBridgeLib.NS_EW:
        if '_'.join([c,d[0]]) in augmented_df.columns:
            augmented_df['_'.join([c,d])] = augmented_df[['_'.join([c,d[0]]),'_'.join([c,d[1]])]].sum(axis='columns').astype(t) # e.g. HCP_NS = HCP_N + HCP_S
        for s in mlBridgeLib.SHDC:
            augmented_df['_'.join([c,d,s])] = augmented_df[['_'.join([c,d[0],s]), '_'.join([c,d[1],s])]].sum(axis='columns').astype(t)
max_ns_ew = [('DD','int8')]
for c,t in max_ns_ew:
    for d in mlBridgeLib.NS_EW:
        for s in mlBridgeLib.CDHSN:
            augmented_df['_'.join([c,d,s])] = augmented_df[['_'.join([c,d[0],s]), '_'.join([c,d[1],s])]].max(axis='columns').astype(t)
augmented_df

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                                Par                                                                         DDmakes  DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N                                                                                            Hands_Bin                                                    HB_N                                                    HB_E                                                    HB_S                                                    HB_W                                                                              HCP  HCP_N  HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  HCP_E  HCP_E_S  HCP_E_H  HCP_E_D  HCP_E_C  HCP_S  HCP_S_S  HCP_S_H  HCP_S_D  HCP_S_C  HCP_W  HCP_W_S  HCP_W_H  HCP_W_D  HCP_W_C                                                                                                   QT  QT_N  QT_N_S  ...  QT_W  QT_W_S  QT_W_H  QT_W_D  QT_W_C                                              Suit_Lengths  SL_N_S  SL_N_H  SL_N_D  SL_N_C  SL_E_S  SL_E_H  SL_E_D  SL_E_C  SL_S_S  SL_S_H  SL_S_D  SL_S_C SL_W_S  SL_W_H  SL_W_D  SL_W_C  HCP_NS  HCP_NS_S  HCP_NS_H  HCP_NS_D  HCP_NS_C  HCP_EW  HCP_EW_S  HCP_EW_H  HCP_EW_D  HCP_EW_C  QT_NS  QT_NS_S  QT_NS_H  QT_NS_D  QT_NS_C  QT_EW  QT_EW_S  QT_EW_H  QT_EW_D  QT_EW_C  SL_NS_S  SL_NS_H  SL_NS_D  SL_NS_C  SL_EW_S  SL_EW_H  SL_EW_D  SL_EW_C  DD_NS_C  DD_NS_D  DD_NS_H  DD_NS_S  DD_NS_N  DD_EW_C  DD_EW_D  DD_EW_H  DD_EW_S  DD_EW_N
0        (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                         (100, [(4, S, *, EW, -1)])        ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2  ((0b100010000010000000001100010000000011001011100100, (0b100010000, 0b100000000011, 0b1000000001...      0b100010000010000000001100010000000011001011100100  0b1000001001010001000000000001100100100100100000001001   0b100000100000100111100010010000000010000000100010010    0b11010000101000000011100000001011001000010000000000   ((9, (0, 3, 1, 5)), (14, (4, 2, 5, 3)), (12, (3, 5, 4, 0)), (5, (3, 0, 0, 2)))      9        0        3        1        5     14        4        2        5        3     12        3        5        4        0      5        3        0        0        2      (6.5, ((1.5, (0, 0.5, 0, 1)), (2.5, (1, 0, 1, 0.5)), (2.5, (0.5, 1, 1, 0)), (0, (0, 0, 0, 0))))  1.50    0.00  ...  0.00    0.00    0.00    0.00    0.00  ((2, 3, 2, 6), (4, 1, 5, 3), (2, 6, 2, 3), (5, 3, 4, 1))       2       3       2       6       4       1       5       3       2       6       2       3      5       3       4       1      21         3         8         5         5      19         7         2         5         5   4.00     0.50     1.50     1.00     1.00   2.50     1.00     0.00     1.00     0.50        4        9        4        9        9        4        9        4       10        4       10        4        8        2        9        3        9        2
1        (acbl, 2620412)          77908    100961    20  200217A_20      W  Both  ST85HKJDJ43CKJ873SQ32HA643DK96CT94SAJ64HT98DT75CA52SK97HQ752DAQ82CQ6  ((T85, KJ, J43, KJ873), (AJ64, T98, T75, A52), (K97, Q752, AQ82, Q6), (Q32, A643, K96, T94))          (90, [(1, D, , NS, 1), (1, C, , NS, 1), (1, N, , NS, 0)])            ((8, 8, 7, 7, 7), (4, 5, 6, 6, 6), (8, 8, 7, 7, 7), (4, 5, 6, 6,

In [17]:
# takes 6s
# Create columns of longest suit.
sl_cols = [('_'.join(['SL_Max',d]),['_'.join(['SL',d,s]) for s in mlBridgeLib.SHDC]) for d in mlBridgeLib.NS_EW]
for d in sl_cols:
    augmented_df[d[0]] = augmented_df[d[1]].idxmax(axis=1).astype('category') # defaults to object so need string or category
augmented_df[[c[0] for c in sl_cols]]

SL_Max_NS SL_Max_EW
0         SL_NS_H   SL_EW_S
1         SL_NS_D   SL_EW_S
2         SL_NS_H   SL_EW_S
3         SL_NS_H   SL_EW_D
4         SL_NS_H   SL_EW_S
5         SL_NS_C   SL_EW_D
6         SL_NS_H   SL_EW_C
7         SL_NS_H   SL_EW_S
8         SL_NS_H   SL_EW_S
9         SL_NS_C   SL_EW_S
10        SL_NS_C   SL_EW_H
11        SL_NS_D   SL_EW_S
12        SL_NS_D   SL_EW_H
13        SL_NS_S   SL_EW_C
14        SL_NS_S   SL_EW_D
15        SL_NS_S   SL_EW_D
16        SL_NS_H   SL_EW_S
17        SL_NS_S   SL_EW_H
18        SL_NS_D   SL_EW_S
19        SL_NS_C   SL_EW_H
20        SL_NS_S   SL_EW_D
21        SL_NS_D   SL_EW_H
22        SL_NS_H   SL_EW_S
23        SL_NS_S   SL_EW_D
24        SL_NS_S   SL_EW_D
...           ...       ...
2761966   SL_NS_H   SL_EW_S
2761967   SL_NS_D   SL_EW_H
2761968   SL_NS_H   SL_EW_C
2761969   SL_NS_H   SL_EW_C
2761970   SL_NS_S   SL_EW_D
2761971   SL_NS_S   SL_EW_C
2761972   SL_NS_S   SL_EW_H
2761973   SL_NS_D   SL_EW_H
2761974   SL_NS_S   SL_EW_D
2761975   SL_NS_H   SL_EW_S
2761976   SL_NS_H   SL_EW_D
2761977   SL_NS_H   SL_EW_S
2761978   SL_NS_D   SL_EW_S
2761979   SL_NS_H   SL_EW_C
2761980   SL_NS_S   SL_EW_D
2761981   SL_NS_D   SL_EW_H
2761982   SL_NS_C   SL_EW_H
2761983   SL_NS_S   SL_EW_D
2761984   SL_NS_C   SL_EW_D
2761985   SL_NS_H   SL_EW_D
2761986   SL_NS_S   SL_EW_H
2761987   SL_NS_C   SL_EW_S
2761988   SL_NS_H   SL_EW_S
2761989   SL_NS_S   SL_EW_H
2761990   SL_NS_S   SL_EW_C

[2761991 rows x 2 columns]

In [18]:
augmented_df.iloc[0][augmented_df.columns.str.startswith('QT')]

QT         (6.5, ((1.5, (0, 0.5, 0, 1)), (2.5, (1, 0, 1, 0.5)), (2.5, (0.5, 1, 1, 0)), (0, (0, 0, 0, 0))))
QT_N                                                                                                  1.50
QT_N_S                                                                                                0.00
QT_N_H                                                                                                0.50
QT_N_D                                                                                                0.00
QT_N_C                                                                                                1.00
QT_E                                                                                                  2.50
QT_E_S                                                                                                1.00
QT_E_H                                                                                                0.00
QT_E_D                               

In [19]:
augmented_df.dtypes

ref                      object
hand_record_id           object
event_id                  int64
Board                    string
EventBoard               string
Dealer                   object
Vul                      object
board_record_string      object
Hands                    object
Par                      object
DDmakes                  object
DD_N_C                     int8
DD_N_D                     int8
DD_N_H                     int8
DD_N_S                     int8
DD_N_N                     int8
DD_E_C                     int8
DD_E_D                     int8
DD_E_H                     int8
DD_E_S                     int8
DD_E_N                     int8
DD_S_C                     int8
DD_S_D                     int8
DD_S_H                     int8
DD_S_S                     int8
                         ...   
QT_EW                   float32
QT_EW_S                 float32
QT_EW_H                 float32
QT_EW_D                 float32
QT_EW_C                 float32
SL_NS_S 

In [20]:
# takes 10s
# Create columns of Par_Score. Give it 'category' dtype.
augmented_df['Par_Score'] = [par[0] for par in augmented_df['Par']]
augmented_df['Par_Score'] = augmented_df['Par_Score'].astype('category') # note: using category for Par_Score
augmented_df

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                                Par                                                                         DDmakes  DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N                                                                                            Hands_Bin                                                    HB_N                                                    HB_E                                                    HB_S                                                    HB_W                                                                              HCP  HCP_N  HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  HCP_E  HCP_E_S  HCP_E_H  HCP_E_D  HCP_E_C  HCP_S  HCP_S_S  HCP_S_H  HCP_S_D  HCP_S_C  HCP_W  HCP_W_S  HCP_W_H  HCP_W_D  HCP_W_C                                                                                                   QT  QT_N  QT_N_S  ...  QT_W_D  QT_W_C                                              Suit_Lengths  SL_N_S  SL_N_H  SL_N_D  SL_N_C  SL_E_S  SL_E_H  SL_E_D  SL_E_C  SL_S_S  SL_S_H  SL_S_D  SL_S_C  SL_W_S  SL_W_H  SL_W_D SL_W_C  HCP_NS  HCP_NS_S  HCP_NS_H  HCP_NS_D  HCP_NS_C  HCP_EW  HCP_EW_S  HCP_EW_H  HCP_EW_D  HCP_EW_C  QT_NS  QT_NS_S  QT_NS_H  QT_NS_D  QT_NS_C  QT_EW  QT_EW_S  QT_EW_H  QT_EW_D  QT_EW_C  SL_NS_S  SL_NS_H  SL_NS_D  SL_NS_C  SL_EW_S  SL_EW_H  SL_EW_D  SL_EW_C  DD_NS_C  DD_NS_D  DD_NS_H  DD_NS_S  DD_NS_N  DD_EW_C  DD_EW_D  DD_EW_H  DD_EW_S  DD_EW_N  SL_Max_NS  SL_Max_EW  Par_Score
0        (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                         (100, [(4, S, *, EW, -1)])        ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2  ((0b100010000010000000001100010000000011001011100100, (0b100010000, 0b100000000011, 0b1000000001...      0b100010000010000000001100010000000011001011100100  0b1000001001010001000000000001100100100100100000001001   0b100000100000100111100010010000000010000000100010010    0b11010000101000000011100000001011001000010000000000   ((9, (0, 3, 1, 5)), (14, (4, 2, 5, 3)), (12, (3, 5, 4, 0)), (5, (3, 0, 0, 2)))      9        0        3        1        5     14        4        2        5        3     12        3        5        4        0      5        3        0        0        2      (6.5, ((1.5, (0, 0.5, 0, 1)), (2.5, (1, 0, 1, 0.5)), (2.5, (0.5, 1, 1, 0)), (0, (0, 0, 0, 0))))  1.50    0.00  ...    0.00    0.00  ((2, 3, 2, 6), (4, 1, 5, 3), (2, 6, 2, 3), (5, 3, 4, 1))       2       3       2       6       4       1       5       3       2       6       2       3       5       3       4      1      21         3         8         5         5      19         7         2         5         5   4.00     0.50     1.50     1.00     1.00   2.50     1.00     0.00     1.00     0.50        4        9        4        9        9        4        9        4       10        4       10        4        8        2        9        3        9        2    SL_NS_H    SL_EW_S        100
1        (acbl, 2620412)          77908    100961    20  200217A_20      W  Both  ST85HKJDJ43CKJ873SQ32HA643DK96CT94SAJ64HT98DT75CA52SK97HQ752DAQ82CQ6  ((T85, KJ, J43, KJ873), (AJ64, T98, T75, A52), (K97, Q752, AQ82, Q6), (Q32, A643, K96, T94))          (90, [(1, D, , NS, 1), (1, C, , NS, 1), (1, N, , NS, 0)])            ((8, 8, 7, 7, 7), (4, 5, 6, 6, 6), (8, 8, 

In [21]:
# takes 45s
# Create column of contract types by partnership by suit. e.g. CT_NS_C.
contract_types_d = mlBridgeLib.CategorifyContractType(augmented_df['DDmakes'])
contract_types_df = pd.DataFrame(contract_types_d,dtype='category')
display(contract_types_df.dtypes,contract_types_df.head())
assert len(augmented_df) == len(contract_types_df)
augmented_df = pd.concat([augmented_df,contract_types_df],axis='columns',join='inner')
del contract_types_df,contract_types_d
display(augmented_df.dtypes,augmented_df)

CT_NS_C    category
CT_NS_D    category
CT_NS_H    category
CT_NS_S    category
CT_NS_N    category
CT_EW_C    category
CT_EW_D    category
CT_EW_H    category
CT_EW_S    category
CT_EW_N    category
dtype: object

CT_NS_C  CT_NS_D  CT_NS_H  CT_NS_S  CT_NS_N  CT_EW_C  CT_EW_D CT_EW_H  CT_EW_S  CT_EW_N
0  Partial     Pass     Game     Pass  Partial     Pass  Partial    Pass  Partial     Pass
1  Partial  Partial  Partial  Partial  Partial     Pass     Pass    Pass     Pass     Pass
2  Partial  Partial  Partial     Pass     Pass     Pass     Pass    Pass  Partial     Pass
3     Pass     Pass     Game  Partial     Pass     Game     Game    Pass     Pass     Game
4     Pass     Pass     Pass     Pass     Pass  Partial     Game    Pass    SSlam  Partial

ref                      object
hand_record_id           object
event_id                  int64
Board                    string
EventBoard               string
Dealer                   object
Vul                      object
board_record_string      object
Hands                    object
Par                      object
DDmakes                  object
DD_N_C                     int8
DD_N_D                     int8
DD_N_H                     int8
DD_N_S                     int8
DD_N_N                     int8
DD_E_C                     int8
DD_E_D                     int8
DD_E_H                     int8
DD_E_S                     int8
DD_E_N                     int8
DD_S_C                     int8
DD_S_D                     int8
DD_S_H                     int8
DD_S_S                     int8
                         ...   
SL_EW_D                    int8
SL_EW_C                    int8
DD_NS_C                    int8
DD_NS_D                    int8
DD_NS_H                    int8
DD_NS_S 

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                                Par                                                                         DDmakes  DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N                                                                                            Hands_Bin                                                    HB_N                                                    HB_E                                                    HB_S                                                    HB_W                                                                              HCP  HCP_N  HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  HCP_E  HCP_E_S  HCP_E_H  HCP_E_D  HCP_E_C  HCP_S  HCP_S_S  HCP_S_H  HCP_S_D  HCP_S_C  HCP_W  HCP_W_S  HCP_W_H  HCP_W_D  HCP_W_C                                                                                                   QT  QT_N  QT_N_S  ...  SL_E_C  SL_S_S  SL_S_H  SL_S_D  SL_S_C  SL_W_S  SL_W_H  SL_W_D  SL_W_C  HCP_NS  HCP_NS_S  HCP_NS_H  HCP_NS_D  HCP_NS_C  HCP_EW  HCP_EW_S  HCP_EW_H  HCP_EW_D HCP_EW_C  QT_NS  QT_NS_S  QT_NS_H  QT_NS_D  QT_NS_C  QT_EW  QT_EW_S  QT_EW_H  QT_EW_D  QT_EW_C  SL_NS_S  SL_NS_H  SL_NS_D  SL_NS_C  SL_EW_S  SL_EW_H  SL_EW_D  SL_EW_C  DD_NS_C  DD_NS_D  DD_NS_H  DD_NS_S  DD_NS_N  DD_EW_C  DD_EW_D  DD_EW_H  DD_EW_S  DD_EW_N  SL_Max_NS  SL_Max_EW  Par_Score  CT_NS_C  CT_NS_D  CT_NS_H  CT_NS_S  CT_NS_N  CT_EW_C  CT_EW_D  CT_EW_H  CT_EW_S  CT_EW_N
0        (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                         (100, [(4, S, *, EW, -1)])        ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2  ((0b100010000010000000001100010000000011001011100100, (0b100010000, 0b100000000011, 0b1000000001...      0b100010000010000000001100010000000011001011100100  0b1000001001010001000000000001100100100100100000001001   0b100000100000100111100010010000000010000000100010010    0b11010000101000000011100000001011001000010000000000   ((9, (0, 3, 1, 5)), (14, (4, 2, 5, 3)), (12, (3, 5, 4, 0)), (5, (3, 0, 0, 2)))      9        0        3        1        5     14        4        2        5        3     12        3        5        4        0      5        3        0        0        2      (6.5, ((1.5, (0, 0.5, 0, 1)), (2.5, (1, 0, 1, 0.5)), (2.5, (0.5, 1, 1, 0)), (0, (0, 0, 0, 0))))  1.50    0.00  ...       3       2       6       2       3       5       3       4       1      21         3         8         5         5      19         7         2         5        5   4.00     0.50     1.50     1.00     1.00   2.50     1.00     0.00     1.00     0.50        4        9        4        9        9        4        9        4       10        4       10        4        8        2        9        3        9        2    SL_NS_H    SL_EW_S        100  Partial     Pass     Game     Pass  Partial     Pass  Partial     Pass  Partial     Pass
1        (acbl, 2620412)          77908    100961    20  200217A_20      W  Both  ST85HKJDJ43CKJ873SQ32HA643DK96CT94SAJ64HT98DT75CA52SK97HQ752DAQ82CQ6  ((T85, KJ, J43, KJ873), (AJ64, T98, T75, A52), (K97, Q752, AQ82, Q6), (Q32, A643, K96, T94))          (90, [(1, D, , NS, 1), (1, C, , NS, 1), (1, N, , NS, 0)])            ((8, 8, 7, 7, 7), (4, 5, 6, 6, 6), (8, 8, 7, 7, 7), (4, 5, 6, 6, 6))       8       8       7       7       7       4      

In [22]:
# takes 15s
# Create columns of contract types by partnership by suit by contract. e.g. CT_NS_C_Game
contract_types_d = {}
cols = augmented_df.filter(regex=r'CT_(NS|EW)_[CDHSN]').columns
for c in cols:
    for t in mlBridgeLib.contract_types:
        print(c,t,len((t == augmented_df[c]).values))
        new_c = c+'_'+t
        contract_types_d[new_c] = (t == augmented_df[c]).values
#contract_types_d = CategorifyContractType(augmented_df['DDmakes'])
contract_types_df = pd.DataFrame(contract_types_d)
display(contract_types_df.dtypes,contract_types_df.head())
assert len(augmented_df) == len(contract_types_df)
augmented_df = pd.concat([augmented_df,contract_types_df],axis='columns',join='inner')
del contract_types_df,contract_types_d
display(augmented_df.dtypes,augmented_df)

CT_NS_C Pass 2761991
CT_NS_C Partial 2761991
CT_NS_C Game 2761991
CT_NS_C SSlam 2761991
CT_NS_C GSlam 2761991
CT_NS_D Pass 2761991
CT_NS_D Partial 2761991
CT_NS_D Game 2761991
CT_NS_D SSlam 2761991
CT_NS_D GSlam 2761991
CT_NS_H Pass 2761991
CT_NS_H Partial 2761991
CT_NS_H Game 2761991
CT_NS_H SSlam 2761991
CT_NS_H GSlam 2761991
CT_NS_S Pass 2761991
CT_NS_S Partial 2761991
CT_NS_S Game 2761991
CT_NS_S SSlam 2761991
CT_NS_S GSlam 2761991
CT_NS_N Pass 2761991
CT_NS_N Partial 2761991
CT_NS_N Game 2761991
CT_NS_N SSlam 2761991
CT_NS_N GSlam 2761991
CT_EW_C Pass 2761991
CT_EW_C Partial 2761991
CT_EW_C Game 2761991
CT_EW_C SSlam 2761991
CT_EW_C GSlam 2761991
CT_EW_D Pass 2761991
CT_EW_D Partial 2761991
CT_EW_D Game 2761991
CT_EW_D SSlam 2761991
CT_EW_D GSlam 2761991
CT_EW_H Pass 2761991
CT_EW_H Partial 2761991
CT_EW_H Game 2761991
CT_EW_H SSlam 2761991
CT_EW_H GSlam 2761991
CT_EW_S Pass 2761991
CT_EW_S Partial 2761991
CT_EW_S Game 2761991
CT_EW_S SSlam 2761991
CT_EW_S GSlam 2761991
CT_EW_N Pa

CT_NS_C_Pass       bool
CT_NS_C_Partial    bool
CT_NS_C_Game       bool
CT_NS_C_SSlam      bool
CT_NS_C_GSlam      bool
CT_NS_D_Pass       bool
CT_NS_D_Partial    bool
CT_NS_D_Game       bool
CT_NS_D_SSlam      bool
CT_NS_D_GSlam      bool
CT_NS_H_Pass       bool
CT_NS_H_Partial    bool
CT_NS_H_Game       bool
CT_NS_H_SSlam      bool
CT_NS_H_GSlam      bool
CT_NS_S_Pass       bool
CT_NS_S_Partial    bool
CT_NS_S_Game       bool
CT_NS_S_SSlam      bool
CT_NS_S_GSlam      bool
CT_NS_N_Pass       bool
CT_NS_N_Partial    bool
CT_NS_N_Game       bool
CT_NS_N_SSlam      bool
CT_NS_N_GSlam      bool
CT_EW_C_Pass       bool
CT_EW_C_Partial    bool
CT_EW_C_Game       bool
CT_EW_C_SSlam      bool
CT_EW_C_GSlam      bool
CT_EW_D_Pass       bool
CT_EW_D_Partial    bool
CT_EW_D_Game       bool
CT_EW_D_SSlam      bool
CT_EW_D_GSlam      bool
CT_EW_H_Pass       bool
CT_EW_H_Partial    bool
CT_EW_H_Game       bool
CT_EW_H_SSlam      bool
CT_EW_H_GSlam      bool
CT_EW_S_Pass       bool
CT_EW_S_Partial 

CT_NS_C_Pass  CT_NS_C_Partial  CT_NS_C_Game  CT_NS_C_SSlam  CT_NS_C_GSlam  CT_NS_D_Pass  CT_NS_D_Partial  CT_NS_D_Game  CT_NS_D_SSlam  CT_NS_D_GSlam  CT_NS_H_Pass  CT_NS_H_Partial  CT_NS_H_Game  CT_NS_H_SSlam  CT_NS_H_GSlam  CT_NS_S_Pass  CT_NS_S_Partial  CT_NS_S_Game  CT_NS_S_SSlam  CT_NS_S_GSlam  CT_NS_N_Pass  CT_NS_N_Partial  CT_NS_N_Game  CT_NS_N_SSlam  CT_NS_N_GSlam  CT_EW_C_Pass  CT_EW_C_Partial  CT_EW_C_Game  CT_EW_C_SSlam  CT_EW_C_GSlam  CT_EW_D_Pass  CT_EW_D_Partial  CT_EW_D_Game  CT_EW_D_SSlam  CT_EW_D_GSlam  CT_EW_H_Pass  CT_EW_H_Partial  CT_EW_H_Game  CT_EW_H_SSlam  CT_EW_H_GSlam  CT_EW_S_Pass  CT_EW_S_Partial  CT_EW_S_Game  CT_EW_S_SSlam  CT_EW_S_GSlam  CT_EW_N_Pass  CT_EW_N_Partial  CT_EW_N_Game  CT_EW_N_SSlam  CT_EW_N_GSlam
0         False             True         False          False          False          True            False         False          False          False         False            False          True          False          False          True            False         False          False          False         False             True         False          False          False          True            False         False          False          False         False             True         False          False          False          True            False         False          False          False         False             True         False          False          False          True            False         False          False          False
1         False             True         False          False          False         False             True         False          False          False         False             True         False          False          False         False             True         False          False          False         False             True         False          False          False          True            False         False          False          False          True            False         False          False          False          True            False         False          False          False          True            False         False          False          False          True            False         False          False          False
2         False             True         False          False          False         False             True         False          False          False         False             True         False          False          False          True            False         False          False          False          True            False         False          False          False          True            False         False          False          False          True            False         False          False          False          True            False         False          False          False         False             True         False          False          False          True            False         False          False          False
3          True            False         False          False          False          True            False         False          False          False         False            False          True          False          False         False             True         False          False          False          True            False         False          False          False         False            False          True          False          False         False            False          True          False          False          True            False         False          False          False          True            False         False          False          False         False            False          True          False          False
4          True            False         False          False          False          True            False         False          False          False          True            False         False          False          False          True   

ref                    object
hand_record_id         object
event_id                int64
Board                  string
EventBoard             string
Dealer                 object
Vul                    object
board_record_string    object
Hands                  object
Par                    object
DDmakes                object
DD_N_C                   int8
DD_N_D                   int8
DD_N_H                   int8
DD_N_S                   int8
DD_N_N                   int8
DD_E_C                   int8
DD_E_D                   int8
DD_E_H                   int8
DD_E_S                   int8
DD_E_N                   int8
DD_S_C                   int8
DD_S_D                   int8
DD_S_H                   int8
DD_S_S                   int8
                        ...  
CT_EW_C_Pass             bool
CT_EW_C_Partial          bool
CT_EW_C_Game             bool
CT_EW_C_SSlam            bool
CT_EW_C_GSlam            bool
CT_EW_D_Pass             bool
CT_EW_D_Partial          bool
CT_EW_D_Ga

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                                Par                                                                         DDmakes  DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N                                                                                            Hands_Bin                                                    HB_N                                                    HB_E                                                    HB_S                                                    HB_W                                                                              HCP  HCP_N  HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  HCP_E  HCP_E_S  HCP_E_H  HCP_E_D  HCP_E_C  HCP_S  HCP_S_S  HCP_S_H  HCP_S_D  HCP_S_C  HCP_W  HCP_W_S  HCP_W_H  HCP_W_D  HCP_W_C                                                                                                   QT  QT_N  QT_N_S  ...  CT_NS_C  CT_NS_D  CT_NS_H  CT_NS_S  CT_NS_N  CT_EW_C  CT_EW_D  CT_EW_H  CT_EW_S  CT_EW_N  CT_NS_C_Pass  CT_NS_C_Partial  CT_NS_C_Game  CT_NS_C_SSlam  CT_NS_C_GSlam  CT_NS_D_Pass  CT_NS_D_Partial  CT_NS_D_Game CT_NS_D_SSlam  CT_NS_D_GSlam  CT_NS_H_Pass  CT_NS_H_Partial  CT_NS_H_Game  CT_NS_H_SSlam  CT_NS_H_GSlam  CT_NS_S_Pass  CT_NS_S_Partial  CT_NS_S_Game  CT_NS_S_SSlam  CT_NS_S_GSlam  CT_NS_N_Pass  CT_NS_N_Partial  CT_NS_N_Game  CT_NS_N_SSlam  CT_NS_N_GSlam  CT_EW_C_Pass  CT_EW_C_Partial  CT_EW_C_Game  CT_EW_C_SSlam  CT_EW_C_GSlam  CT_EW_D_Pass  CT_EW_D_Partial  CT_EW_D_Game  CT_EW_D_SSlam  CT_EW_D_GSlam  CT_EW_H_Pass  CT_EW_H_Partial  CT_EW_H_Game  CT_EW_H_SSlam  CT_EW_H_GSlam  CT_EW_S_Pass  CT_EW_S_Partial  CT_EW_S_Game  CT_EW_S_SSlam  CT_EW_S_GSlam  CT_EW_N_Pass  CT_EW_N_Partial  CT_EW_N_Game  CT_EW_N_SSlam  CT_EW_N_GSlam
0        (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                         (100, [(4, S, *, EW, -1)])        ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2  ((0b100010000010000000001100010000000011001011100100, (0b100010000, 0b100000000011, 0b1000000001...      0b100010000010000000001100010000000011001011100100  0b1000001001010001000000000001100100100100100000001001   0b100000100000100111100010010000000010000000100010010    0b11010000101000000011100000001011001000010000000000   ((9, (0, 3, 1, 5)), (14, (4, 2, 5, 3)), (12, (3, 5, 4, 0)), (5, (3, 0, 0, 2)))      9        0        3        1        5     14        4        2        5        3     12        3        5        4        0      5        3        0        0        2      (6.5, ((1.5, (0, 0.5, 0, 1)), (2.5, (1, 0, 1, 0.5)), (2.5, (0.5, 1, 1, 0)), (0, (0, 0, 0, 0))))  1.50    0.00  ...  Partial     Pass     Game     Pass  Partial     Pass  Partial     Pass  Partial     Pass         False             True         False          False          False          True            False         False         False          False         False            False          True          False          False          True            False         False          False          False         False             True         False          False          False          True            False         False          False          False         False             True         False          False          False          True            False         False          False         

In [23]:
# todo: problem is there can be multiple par contracts, multiple directions, multiple results (down 1, make 400, etc.)
#augmented_df['Par_Level'] = [par[0] for par in augmented_df['Par']]
#augmented_df
#augmented_df['Par_Suit'] = [par[0] for par in augmented_df['Par']]
#augmented_df
#augmented_df['Par_Dir'] = [par[0] for par in augmented_df['Par']]
#augmented_df
#augmented_df['Par_Result'] = [par[0] for par in augmented_df['Par']]
#augmented_df

In [24]:
# takes 10s
# Create columns of vulnerability by partnership.
augmented_df['Vul_NS'] = augmented_df['Vul'].isin(['N_S','Both'])
augmented_df['Vul_EW'] = augmented_df['Vul'].isin(['E_W','Both'])
augmented_df

ref hand_record_id  event_id Board  EventBoard Dealer   Vul                                                   board_record_string                                                                                         Hands                                                                Par                                                                         DDmakes  DD_N_C  DD_N_D  DD_N_H  DD_N_S  DD_N_N  DD_E_C  DD_E_D  DD_E_H  DD_E_S  DD_E_N  DD_S_C  DD_S_D  DD_S_H  DD_S_S  DD_S_N  DD_W_C  DD_W_D  DD_W_H  DD_W_S  DD_W_N                                                                                            Hands_Bin                                                    HB_N                                                    HB_E                                                    HB_S                                                    HB_W                                                                              HCP  HCP_N  HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  HCP_E  HCP_E_S  HCP_E_H  HCP_E_D  HCP_E_C  HCP_S  HCP_S_S  HCP_S_H  HCP_S_D  HCP_S_C  HCP_W  HCP_W_S  HCP_W_H  HCP_W_D  HCP_W_C                                                                                                   QT  QT_N  QT_N_S  ...  CT_NS_H  CT_NS_S  CT_NS_N  CT_EW_C  CT_EW_D  CT_EW_H  CT_EW_S  CT_EW_N  CT_NS_C_Pass  CT_NS_C_Partial  CT_NS_C_Game  CT_NS_C_SSlam  CT_NS_C_GSlam  CT_NS_D_Pass  CT_NS_D_Partial  CT_NS_D_Game  CT_NS_D_SSlam  CT_NS_D_GSlam CT_NS_H_Pass  CT_NS_H_Partial  CT_NS_H_Game  CT_NS_H_SSlam  CT_NS_H_GSlam  CT_NS_S_Pass  CT_NS_S_Partial  CT_NS_S_Game  CT_NS_S_SSlam  CT_NS_S_GSlam  CT_NS_N_Pass  CT_NS_N_Partial  CT_NS_N_Game  CT_NS_N_SSlam  CT_NS_N_GSlam  CT_EW_C_Pass  CT_EW_C_Partial  CT_EW_C_Game  CT_EW_C_SSlam  CT_EW_C_GSlam  CT_EW_D_Pass  CT_EW_D_Partial  CT_EW_D_Game  CT_EW_D_SSlam  CT_EW_D_GSlam  CT_EW_H_Pass  CT_EW_H_Partial  CT_EW_H_Game  CT_EW_H_SSlam  CT_EW_H_GSlam  CT_EW_S_Pass  CT_EW_S_Partial  CT_EW_S_Game  CT_EW_S_SSlam  CT_EW_S_GSlam  CT_EW_N_Pass  CT_EW_N_Partial  CT_EW_N_Game  CT_EW_N_SSlam  CT_EW_N_GSlam  Vul_NS  Vul_EW
0        (acbl, 2620401)          77908    100961    09  200217A_09      N   E_W  ST6HK32DJ2CAJ9874SQJ942H765DT874CQSA853HQDKQ963CK52SK7HAJT984DA5CT63  ((T6, K32, J2, AJ9874), (A853, Q, KQ963, K52), (K7, AJT984, A5, T63), (QJ942, 765, T874, Q))                                         (100, [(4, S, *, EW, -1)])        ((10, 4, 10, 4, 8), (2, 9, 3, 9, 2), (10, 4, 10, 4, 8), (2, 9, 3, 9, 2))      10       4      10       4       8       2       9       3       9       2      10       4      10       4       8       2       9       3       9       2  ((0b100010000010000000001100010000000011001011100100, (0b100010000, 0b100000000011, 0b1000000001...      0b100010000010000000001100010000000011001011100100  0b1000001001010001000000000001100100100100100000001001   0b100000100000100111100010010000000010000000100010010    0b11010000101000000011100000001011001000010000000000   ((9, (0, 3, 1, 5)), (14, (4, 2, 5, 3)), (12, (3, 5, 4, 0)), (5, (3, 0, 0, 2)))      9        0        3        1        5     14        4        2        5        3     12        3        5        4        0      5        3        0        0        2      (6.5, ((1.5, (0, 0.5, 0, 1)), (2.5, (1, 0, 1, 0.5)), (2.5, (0.5, 1, 1, 0)), (0, (0, 0, 0, 0))))  1.50    0.00  ...     Game     Pass  Partial     Pass  Partial     Pass  Partial     Pass         False             True         False          False          False          True            False         False          False          False        False            False          True          False          False          True            False         False          False          False         False             True         False          False          False          True            False         False          False          False         False             True         False          False          False          True            False         False          False          False         False

In [25]:
# Create views of train/validate split.
# todo: validate shapes, validate columns are only numeric or boolean
def create_train_valid_dfs(augmented_df, training_columns_regex, split, dep_var):

    training_df = augmented_df.filter(regex=training_columns_regex, axis='columns')
    print('Training columns:', training_df.columns)

    # why is this failing?
    #assert training_df.isna().any().any()

    # create training dataframes
    trainx = training_df[split].drop(dep_var,axis='columns')
    display(f'trainx: dtypes:{trainx.dtypes} len:{len(trainx)} shape:{trainx.shape}',trainx.head())
    assert (trainx.dtypes != 'object').all()
    trainy = training_df[split][dep_var]
    display(f'trainy: dtypes:{trainy.dtypes} len:{len(trainy)} shape:{trainy.shape}',trainy.head())
    assert trainy.dtype != 'object'

    #assert dep_var in trainx.columns # dep_var must be in training df
    assert dep_var == trainy.name # dep_var must be in training df

    # construct validation dataframes
    validx = training_df[~split].drop(dep_var,axis='columns')
    display(f'validx: dtypes:{validx.dtypes} len:{len(validx)} shape:{validx.shape}',validx.head())
    assert (validx.dtypes != 'object').all()
    validy = training_df[~split][dep_var]
    display(f'validy: dtypes:{validy.dtypes} len:{len(validy)} shape:{validy.shape}',validy.head())
    assert validy.dtype != 'object'

    #assert dep_var not in validx.columns # dep_var must not be in validation df
    assert dep_var == validy.name # dep_var must not be in validation df

    return trainx, trainy, validx, validy

In [26]:
import sklearn.pipeline
import sklearn.preprocessing
import sklearn.neural_network
import sklearn.compose

def Train(estimator, dep_var, trainx, trainy, validx, validy, **kwargs):

    column_transformers = []
    all_columns = []
    passthrough_columns = []
    # how to specify columns to be OneHotEncoded? ('ohe',sklearn.preprocessing.OneHotEncoder())
    pipes = [('boolean',None),('category',sklearn.preprocessing.OrdinalEncoder()),('number',sklearn.preprocessing.StandardScaler()),('string',sklearn.preprocessing.OrdinalEncoder())]
    for dt,p in pipes:
        columns = trainx.select_dtypes(dt).columns.to_list()
        print(f'{dt}:{columns}')
        if len(columns) > 0:
            if p is None:
                passthrough_columns += columns
            else:
                pipeline = sklearn.pipeline.Pipeline(steps=[(dt, p)])
                column_transformers.append((dt,pipeline,columns))
            all_columns += columns
    if len(passthrough_columns) > 0:
        column_transformers.append(('passthrough','passthrough',passthrough_columns))

    assert sorted(all_columns) == sorted(trainx.columns.to_list())

    preprocessor_pipeline = sklearn.compose.ColumnTransformer(column_transformers)

    if estimator == 'LinearRegression':
        estimator_func = sklearn.neural_network.LinearRegression(random_state=1, **kwargs)
    elif estimator == 'LogisticRegressionClassifier':
        estimator_func = sklearn.neural_network.LogisticRegressionClassifier(random_state=1, **kwargs)
    elif estimator == 'MLPClassifier':
        estimator_func = sklearn.neural_network.MLPClassifier(random_state=1, **kwargs)
    elif estimator == 'MLPRegressor':
        estimator_func = sklearn.neural_network.MLPRegressor(random_state=1, **kwargs)
    else:
        assert 'Unknown Estimator', estimator
    
    m = sklearn.pipeline.Pipeline(steps=[
        ('preprocessor', preprocessor_pipeline),
        ('estimator', estimator_func)
    ])

    m.fit(trainx, trainy)
    predictionsEmbedded = m.predict(validx)
    probabilities = m.predict_proba(validx)
    predictionsCoefficientsdf = pd.DataFrame(m['estimator'].coefs_[0].T, columns=validx.columns)

    assert len(predictionsEmbedded) == len(validy)

    return m, predictionsEmbedded, probabilities, predictionsCoefficientsdf

In [27]:
# takes 1m30s
# save augmented_df
augmented_standardized_hand_records_file = acblPath.joinpath('acbl_hand_records_augmented.pkl')
with open(augmented_standardized_hand_records_file, 'wb') as f:
    pickle.dump(augmented_df, f)
print(f"Saved {augmented_standardized_hand_records_file}: size:{augmented_standardized_hand_records_file.stat().st_size}")

Saved e:\bridge\data\acbl\acbl_hand_records_augmented.pkl: size:3658853355


In [28]:
# takes 35s
# load augmented_df
augmented_standardized_hand_records_file = acblPath.joinpath('acbl_hand_records_augmented.pkl')
with open(augmented_standardized_hand_records_file, 'rb') as f:
    augmented_df = pickle.load(f)

In [29]:
# takes 30m to 90m
# 1) Select: dependent variable, columns for training, estimator.
# 2) Call train/valid split routine.
# 3) Call estimator
# 4) Save model
# takes 12m for 'DD_N_C' with max_iter=200 hidden_layer_sizes=(400, 100).
# takes 40m for 'Par_Score' with max_iter=200 hidden_layer_sizes=(400, 100). No convergence.
# takes 75m for 'Par_Score' with max_iter=500 hidden_layer_sizes=(600, 200). No convergence.

max_iter = 200 # max_iter maximum is 200. setting to smaller number not terminating earlier?
hidden_layer_sizes = (400, 200, 100) # todo: make global was 400,100

# select columns to train on.
training_columns = []
training_columns += ['Vul_(NS|EW)'] # all players know this info
# instead of HCP and QT, use one hot encoded list (52) of North hand?
training_columns += ['(HCP|QT|SL)_N_[SDHC]'] # players know their own hand. we'll use North.
training_columns += ['SL_Max_(NS|EW)'] # column name of longest suit fit. using higher ranking suit if tied.
training_columns += ['HCP_(NS|EW)','SL_(NS|EW)'] # players can somewhat infer this info from bidding
#training_columns += ['DD_(NS|EW)_[CDHSN]','CT_(NS|EW)_[CDHSN]','QT_(NS|EW)_[SHDC]'] # more difficult to infer\
training_columns += ['Par_Score']
training_columns_regex = '|'.join(['^'+fc+'$' for fc in training_columns]) # set regex anchors so entire string is matched

estimator = 'MLPClassifier'

# todo: allow dep_vars that are not in training_columns. 
dep_vars =  ['Par_Score'] # ['DD_NS_C']

for dep_var in dep_vars:

    # Create model's filename using unique values: iteration count, hidden layer sizes.
    saved_model_file = savedModelsPath.joinpath('_'.join([dep_var,str(max_iter)+'Iters','x'.join(str(hls) for hls in hidden_layer_sizes)])+'.pkl')

    # delete outputs
    print(f"Deleting model:{saved_model_file}")
    saved_model_file.unlink(missing_ok=True)

    # define train/validate split
    split = augmented_df['EventBoard']<"21"
    trainx, trainy, validx, validy = create_train_valid_dfs(augmented_df, training_columns_regex, split, dep_var)
    
    # train model
    m, predictionsEmbedded, probabilities, predictionsCoefficientsdf = Train(estimator, dep_var, trainx, trainy, validx, validy, max_iter=max_iter, hidden_layer_sizes=hidden_layer_sizes)
    print(f"model score:{m.score(validx,validy)}")
    
    # save model
    print(f"Saving model: {saved_model_file}")
    saved_model = {'dep_var':dep_var,'trainx':trainx, 'trainy':trainy, 'validx':validx, 'validy':validy, 'm':m, 'predictionsEmbedded':predictionsEmbedded, 'probabilities':probabilities, 'predictionsCoefficientsdf':predictionsCoefficientsdf, 'max_iter':max_iter, 'hidden_layer_sizes':hidden_layer_sizes}
    with open(saved_model_file, 'wb') as f:
        pickle.dump(saved_model, f)
    print(f"Saved model size:{saved_model_file.stat().st_size}")
    
    # load model
    print(f"Loading model: {saved_model_file}")
    with open(saved_model_file, 'rb') as f:
        saved_model = pickle.load(f)
    dep_var, trainx, trainy, validx, validy, m, predictionsEmbedded, probabilities, predictionsCoefficientsdf, max_iter, hidden_layer_sizes = saved_model.values()
    
    # save again using filename of 'LatestModel.pkl'
    latest_model_file = savedModelsPath.joinpath('LatestModel.pkl')
    print(f"Saving model: {latest_model_file}")
    with open(latest_model_file, 'wb') as f:
        pickle.dump(saved_model, f)
    print(f"Latest model size:{latest_model_file.stat().st_size}")

Deleting model:e:\bridge\data\acbl\SavedModels\Par_Score_200Iters_400x200x100.pkl
Training columns: Index(['HCP_N_S', 'HCP_N_H', 'HCP_N_D', 'HCP_N_C', 'QT_N_S', 'QT_N_H',
       'QT_N_D', 'QT_N_C', 'SL_N_S', 'SL_N_H', 'SL_N_D', 'SL_N_C', 'HCP_NS',
       'HCP_EW', 'SL_Max_NS', 'SL_Max_EW', 'Par_Score', 'Vul_NS', 'Vul_EW'],
      dtype='object')


'trainx: dtypes:HCP_N_S          int8\nHCP_N_H          int8\nHCP_N_D          int8\nHCP_N_C          int8\nQT_N_S        float32\nQT_N_H        float32\nQT_N_D        float32\nQT_N_C        float32\nSL_N_S           int8\nSL_N_H           int8\nSL_N_D           int8\nSL_N_C           int8\nHCP_NS           int8\nHCP_EW           int8\nSL_Max_NS    category\nSL_Max_EW    category\nVul_NS           bool\nVul_EW           bool\ndtype: object len:2536687 shape:(2536687, 18)'

HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  QT_N_S  QT_N_H  QT_N_D  QT_N_C  SL_N_S  SL_N_H  SL_N_D  SL_N_C  HCP_NS  HCP_EW SL_Max_NS SL_Max_EW  Vul_NS  Vul_EW
0        0        3        1        5    0.00    0.50    0.00    1.00       2       3       2       6      21      19   SL_NS_H   SL_EW_S   False    True
1        0        4        1        4    0.00    0.50    0.00    0.50       3       2       3       5      22      18   SL_NS_D   SL_EW_S    True    True
2        0        0        6        3    0.00    0.00    1.50    0.00       1       3       4       5      23      17   SL_NS_H   SL_EW_S   False    True
3        0        3        1        1    0.00    0.00    0.00    0.00       1       6       2       4      12      28   SL_NS_H   SL_EW_D    True   False
4        0        2        0        7    0.00    0.00    0.00    2.00       1       5       2       5      13      27   SL_NS_H   SL_EW_S    True    True

'trainy: dtypes:category len:2536687 shape:(2536687,)'

0     100
1      90
2     100
3    -300
4   -1430
Name: Par_Score, dtype: category
Categories (75, int64): [-2220, -2210, -2140, -2000, ..., 2000, 2140, 2210, 2220]

...

HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  QT_N_S  QT_N_H  QT_N_D  QT_N_C  SL_N_S  SL_N_H  SL_N_D  SL_N_C  HCP_NS  HCP_EW SL_Max_NS SL_Max_EW  Vul_NS  Vul_EW
5012        0        0        5        6    0.00    0.00    1.00    1.50       1       2       6       4      25      15   SL_NS_D   SL_EW_S    True    True
5013        0        4        1        4    0.00    0.50    0.00    1.00       0       4       2       7      19      21   SL_NS_C   SL_EW_S    True    True
5014        0        6        0        3    0.00    1.50    0.00    0.50       2       4       3       4      19      21   SL_NS_H   SL_EW_D    True    True
5015        3        0        7        0    0.00    0.00    1.50    0.00       5       3       4       1      20      20   SL_NS_H   SL_EW_C    True    True
5016        4        1        3        0    1.00    0.00    0.00    0.00       3       2       5       3      19      21   SL_NS_D   SL_EW_C    True    True

'validy: dtypes:category len:225304 shape:(225304,)'

5012    630
5013   -110
5014   -120
5015    600
5016   -130
Name: Par_Score, dtype: category
Categories (75, int64): [-2220, -2210, -2140, -2000, ..., 2000, 2140, 2210, 2220]

boolean:['Vul_NS', 'Vul_EW']
category:['SL_Max_NS', 'SL_Max_EW']
number:['HCP_N_S', 'HCP_N_H', 'HCP_N_D', 'HCP_N_C', 'QT_N_S', 'QT_N_H', 'QT_N_D', 'QT_N_C', 'SL_N_S', 'SL_N_H', 'SL_N_D', 'SL_N_C', 'HCP_NS', 'HCP_EW']
string:[]
model score:0.16915367680999893
Saving model: e:\bridge\data\acbl\SavedModels\Par_Score_200Iters_400x200x100.pkl


FileNotFoundError: [Errno 2] No such file or directory: 'e:\\bridge\\data\\acbl\\SavedModels\\Par_Score_200Iters_400x200x100.pkl'

In [31]:
probabilities.shape, len(probabilities), len(validx)

((225304, 75), 225304, 225304)

In [32]:
#assert probabilities.shape == (len(validx), 14)

In [33]:
m, predictionsEmbedded, probabilities, predictionsCoefficientsdf

(Pipeline(steps=[('preprocessor',
                  ColumnTransformer(transformers=[('category',
                                                   Pipeline(steps=[('category',
                                                                    OrdinalEncoder())]),
                                                   ['SL_Max_NS', 'SL_Max_EW']),
                                                  ('number',
                                                   Pipeline(steps=[('number',
                                                                    StandardScaler())]),
                                                   ['HCP_N_S', 'HCP_N_H',
                                                    'HCP_N_D', 'HCP_N_C',
                                                    'QT_N_S', 'QT_N_H', 'QT_N_D',
                                                    'QT_N_C', 'SL_N_S', 'SL_N_H',
                                                    'SL_N_D', 'SL_N_C', 'HCP_NS',
                                

In [34]:
predictionsCoefficientsdf

HCP_N_S  HCP_N_H  HCP_N_D  HCP_N_C  QT_N_S  QT_N_H  QT_N_D  QT_N_C  SL_N_S  SL_N_H  SL_N_D  SL_N_C  HCP_NS  HCP_EW  SL_Max_NS  SL_Max_EW  Vul_NS  Vul_EW
0      -1.27     0.98     0.59     0.63   -0.33    0.14    1.00   -0.02   -1.10   -1.44   -0.56    0.16   -0.24    0.57      -0.07       0.11   -0.69    0.04
1      -1.84    -0.07    -1.16     0.29   -0.59    3.53    0.18    0.30   -0.99   -1.41    1.66    0.46    0.27   -1.86       0.02       0.10   -4.48   -1.18
2      -2.10    -1.56     0.60     1.75    1.76   -0.18   -2.30    0.34    0.29   -0.98    0.63   -0.07   -1.37    0.88      -0.00       0.14   -0.62   -0.67
3      -0.09     1.01     1.35    -0.65    1.55   -0.11    0.48   -0.49   -0.75    0.01   -0.87    0.39   -0.02    0.45      -0.83       0.76   -2.96   -1.00
4      -0.34    -0.13    -0.73     0.87    0.01   -0.40   -0.81   -0.96   -0.38    0.05    1.50   -1.50    0.56   -0.60      -0.51       0.49   -2.04    1.42
5      -2.34     0.79    -0.14     0.46    1.90    1.05   -0.38    0.39   -1.33   -0.09   -0.25   -0.64    1.48   -1.08      -0.48       0.51   -1.39   -0.39
6      -0.59    -0.83    -1.42    -0.25    0.45   -0.36    0.88   -1.62   -0.82   -0.38   -0.72   -0.46    1.36   -0.35      -0.17       0.28   -0.37    0.12
7       0.05    -0.38    -1.66     1.18   -0.65   -0.71    0.81   -0.16    0.64    1.16    0.65    1.23    0.72   -2.41      -0.06      -0.14   -0.58   -1.30
8       0.21    -0.08     0.06     0.84   -0.79   -1.56   -0.36    0.02    0.20    0.83   -0.92   -1.50    0.91    1.49       0.64      -0.53   -1.19   -0.33
9       0.15    -0.10    -0.45     0.93    0.16    0.26    0.20   -1.27   -0.99    0.10    0.50    0.26   -1.25    0.58      -0.90       0.81   -1.24    0.72
10      0.39    -2.89    -2.44    -0.42    1.53    0.74    0.41   -0.15    0.40    1.50    0.07   -0.24   -0.04    0.54      -0.92       1.00   -0.88   -1.13
11      0.09    -0.20    -1.92    -0.38    1.07    0.64    2.33    0.63   -0.01    0.23    0.25   -0.08   -0.53    0.41      -0.49       0.55    0.96   -1.60
12     -0.43     0.74     1.96     0.25   -2.07    0.09   -2.25   -0.14   -0.71    0.03    0.46   -0.37    0.77   -0.68       0.09      -0.25   -0.54   -0.81
13      0.15     0.16    -1.62    -0.62    0.56    0.41    0.61   -1.18   -1.06   -0.40    0.37    0.46   -0.81    0.09       0.35      -0.45   -1.91    1.67
14     -1.03     0.27     1.08    -1.06   -1.09   -2.19   -1.14    0.55    0.99    0.58    0.96    0.54    0.14   -1.40      -0.10       0.12   -0.11   -0.32
15      0.67    -0.64    -1.28    -1.31   -0.17   -1.78   -1.14   -1.18   -0.77    0.44    0.46    0.29   -0.87    0.13       0.51      -0.37   -1.35   -1.59
16     -0.05     1.34    -1.70    -0.14   -1.25    0.07    1.76   -0.37    1.28    0.20    0.43    0.08   -0.60   -0.00       0.71      -0.66   -0.85   -2.03
17      0.01    -0.98    -1.36     1.76    1.05    0.61    0.25   -0.03   -1.42   -0.35    0.14   -0.54    0.06    0.13      -0.87       0.88    0.92   -1.65
18     -0.73     0.68    -0.09     1.56    0.30    1.07   -0.56   -0.80   -0.41   -1.19    0.50   -0.48   -0.70    0.78      -0.27       0.22   -1.36    0.80
19      0.07     0.13    -1.03    -0.83    0.52   -0.52    2.10    0.76   -1.09   -0.49   -0.43    0.09    0.06    0.36       0.15      -0.21   -1.78    0.74
20      0.59    -1.48     1.28    -1.40    0.18    1.09   -1.91    2.10    0.32   -1.74   -0.49   -0.18    0.43    0.20       0.04      -0.19    1.45    1.52
21      0.17    -0.80     1.69    -0.35    1.13    0.56   -2.19    0.27   -1.27   -0.84   -1.26    0.12    1.19   -0.11       0.19      -0.25   -0.27    0.54
22      0.48    -0.73    -0.00    -0.84   -0.48   -0.07   -0.31    0.60   -0.04   -0.63   -0.77   -0.96    0.77    0.95       1.57      -1.56    0.48   -1.82
23     -0.18    -0.70    -0.40    -1.03    1.40    1.38    0.29    0.10   -0.97   -0.76    1.13   -0.00   -0.96   -0.30      -0.65       0.58    1.06   -0.28
24      1.12    -0.31     0.72     2.08    1.15   -1.08

In [35]:
[p for p in predictionsEmbedded]

[400,
 100,
 420,
 100,
 100,
 100,
 -100,
 400,
 -400,
 140,
 -140,
 -500,
 920,
 1510,
 -140,
 140,
 990,
 140,
 -140,
 -400,
 400,
 -430,
 140,
 -450,
 420,
 -110,
 -90,
 1400,
 100,
 -400,
 500,
 100,
 -400,
 -140,
 650,
 500,
 -1520,
 450,
 110,
 450,
 980,
 430,
 100,
 -420,
 460,
 140,
 -100,
 -2220,
 980,
 400,
 -500,
 -100,
 -100,
 400,
 430,
 100,
 -140,
 100,
 140,
 -450,
 420,
 420,
 100,
 650,
 -450,
 -420,
 -130,
 630,
 140,
 140,
 600,
 2210,
 430,
 420,
 -100,
 300,
 -100,
 130,
 100,
 -450,
 -990,
 -140,
 100,
 -450,
 -140,
 -100,
 -100,
 -100,
 650,
 140,
 90,
 1440,
 -130,
 -110,
 420,
 100,
 400,
 1440,
 -420,
 420,
 -120,
 140,
 -420,
 420,
 -400,
 -420,
 980,
 140,
 450,
 100,
 -460,
 300,
 450,
 -140,
 -110,
 -400,
 430,
 400,
 450,
 -500,
 420,
 -1370,
 430,
 -100,
 -600,
 450,
 -460,
 140,
 100,
 130,
 100,
 -400,
 -130,
 -140,
 140,
 -400,
 500,
 -140,
 630,
 100,
 -110,
 100,
 100,
 100,
 100,
 -450,
 -140,
 -140,
 400,
 100,
 -650,
 -990,
 110,
 420,
 -100,


In [36]:
[p for p in probabilities]

[array([1.13575182e-009, 5.47583441e-008, 2.15053304e-013, 1.01324960e-014,
        8.92047897e-014, 3.83094659e-019, 5.23900455e-007, 5.06279511e-008,
        1.20691448e-015, 1.33545746e-007, 1.52771338e-008, 2.44688081e-007,
        6.01898512e-010, 2.55348786e-006, 2.53236306e-007, 3.59007182e-005,
        4.60279322e-008, 3.21591809e-005, 1.87934952e-009, 2.57280967e-006,
        5.93314370e-008, 7.12371173e-005, 1.79778093e-009, 3.36645835e-004,
        3.65591943e-007, 1.64078532e-004, 1.26366671e-005, 1.54417322e-003,
        1.91731506e-004, 5.79361400e-004, 2.05023674e-005, 2.98310404e-006,
        4.45508454e-005, 7.24453851e-003, 1.09597519e-005, 9.33087767e-007,
        5.77437652e-013, 1.90179788e-116, 1.54173776e-010, 1.61991024e-006,
        4.77760282e-004, 2.49671093e-002, 4.88040465e-003, 1.45285132e-002,
        6.12331906e-002, 1.87959660e-002, 1.45628874e-003, 3.89179000e-002,
        2.33834836e-001, 4.79847271e-002, 1.80934124e-001, 1.40959384e-002,
        5.50

In [37]:
apdf = pd.DataFrame({'Actual_Par_Score':validy,'Pred_Par_Score':predictionsEmbedded})
apdf['Actual_Par_Score'] = apdf['Actual_Par_Score'].astype('int16')

In [38]:
apdf['Actual_Pred_Diff_Par_Score'] = (apdf['Actual_Par_Score']-apdf['Pred_Par_Score'])
apdf['Actual_Pred_Diff_Par_Score'].value_counts()

 0       38111
 30      10335
-30       7999
 10       6410
-280      5874
-200      5796
 20       5742
-10       5467
 40       5350
-20       5253
 200      5228
 280      3938
-40       3482
-240      3214
-230      3146
-530      3017
-520      2815
-210      2790
 230      2748
-310      2424
 530      2330
 240      2325
 210      2213
 520      2098
-300      1942
         ...  
-2000        2
 2080        2
 1130        2
-1870        1
 2330        1
-1450        1
-2090        1
 1390        1
-1840        1
 2010        1
-1530        1
 1190        1
-1380        1
-1430        1
 1320        1
 1810        1
-2340        1
-2040        1
-1910        1
 1630        1
-1640        1
 1210        1
 2350        1
-1930        1
 2090        1
Name: Actual_Pred_Diff_Par_Score, Length: 354, dtype: int64